# 18.12.18
create shapes.txt from route geojsons

In [1]:
import json
# import os
# import time, datetime
from collections import OrderedDict
from math import sin, cos, sqrt, atan2, radians
import pandas as pd
import csv


In [2]:
outputFolder = 'gtfs/'

## custom function 
.. that'll do the legwork of turning geojson into array as per shapes.txt  
https://developers.google.com/transit/gtfs/reference/#shapestxt

In [3]:
def geoJson2shape(route_id, shapefile, shapefileRev=None):
	with open(shapefile, encoding='utf8') as f:
		# loading geojson, from https://gis.stackexchange.com/a/73771/44746
		data = json.load(f)
	logmessage('Loaded',shapefile)
		
	output_array = []
	try:
		coordinates = data['features'][0]['geometry']['coordinates']
	except:
		logmessage('Invalid geojson file ' + shapefile)
		return False

	prevlat = coordinates[0][1]
	prevlon = coordinates[0][0]
	dist_traveled = 0
	i = 0
	for item in coordinates:
		newrow = OrderedDict()
		newrow['shape_id'] = route_id + '_0'
		newrow['shape_pt_lat'] = item[1]
		newrow['shape_pt_lon'] = item[0]

		calcdist = lat_long_dist(prevlat,prevlon,item[1],item[0])
		dist_traveled = dist_traveled + calcdist
		newrow['shape_dist_traveled'] = float(format( dist_traveled , '.2f' )) 
		#rounding. From https://stackoverflow.com/a/28142318/4355695

		i = i + 1
		newrow['shape_pt_sequence'] = i
		output_array.append(newrow)
		prevlat = item[1]
		prevlon = item[0]
	
	# Reverse trip now.. either same shapefile in reverse or a different shapefile	
	if( shapefileRev ):
		with open(shapefileRev, encoding='utf8') as g:
			data2 = json.load(g)
		logmessage('Loaded',shapefileRev)
		try:
			coordinates = data2['features'][0]['geometry']['coordinates']
		except:
			logmessage('Invalid geojson file ' + shapefileRev)
			return False
	else:
		coordinates.reverse()
	
	prevlat = coordinates[0][1]
	prevlon = coordinates[0][0]
	dist_traveled = 0
	i = 0
	for item in coordinates:
		newrow = OrderedDict()
		newrow['shape_id'] = route_id + '_1'
		newrow['shape_pt_lat'] = item[1]
		newrow['shape_pt_lon'] = item[0]

		calcdist = lat_long_dist(prevlat,prevlon,item[1],item[0])
		dist_traveled = float(format( dist_traveled + calcdist , '.2f' )) 
		newrow['shape_dist_traveled'] = float(format( dist_traveled , '.2f' )) 
		#rounding. From https://stackoverflow.com/a/28142318/4355695

		i = i + 1
		newrow['shape_pt_sequence'] = i
		output_array.append(newrow)
		prevlat = item[1]
		prevlon = item[0]
	
	return output_array

## supporting functions

In [4]:
def logmessage( *content ):
	# from https://stackoverflow.com/a/26455617/4355695
	line = ' '.join(str(x) for x in list(content))
	print(line) # print to screen also

def lat_long_dist(lat1,lon1,lat2,lon2):
	# function for calculating ground distance between two lat-long locations
	R = 6373.0 # approximate radius of earth in km. 

	lat1 = radians( float(lat1) )
	lon1 = radians( float(lon1) )
	lat2 = radians( float(lat2) )
	lon2 = radians( float(lon2) )

	dlon = lon2 - lon1
	dlat = lat2 - lat1

	a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
	c = 2 * atan2(sqrt(a), sqrt(1 - a))

	# distance = float(format( R * c , '.2f' )) #rounding. From https://stackoverflow.com/a/28142318/4355695
	distance = R * c
	return distance

## first for for RED line

In [5]:
route_id = 'RED'
shapefile = 'red-extended.geojson'

In [6]:
shapeArray = geoJson2shape(route_id, shapefile)

Loaded red-extended.geojson


In [7]:
dfRed = pd.DataFrame(shapeArray)
dfRed

shape_id  shape_pt_lat  shape_pt_lon  shape_dist_traveled  \
0      RED_0     17.496540     78.373026                 0.00   
1      RED_0     17.496535     78.373836                 0.09   
2      RED_0     17.496591     78.374322                 0.14   
3      RED_0     17.496714     78.374809                 0.19   
4      RED_0     17.496896     78.375391                 0.26   
5      RED_0     17.497241     78.377090                 0.44   
6      RED_0     17.497711     78.378221                 0.57   
7      RED_0     17.498883     78.380592                 0.85   
8      RED_0     17.499344     78.381910                 1.00   
9      RED_0     17.499426     78.382398                 1.06   
10     RED_0     17.499448     78.382787                 1.10   
11     RED_0     17.499434     78.382950                 1.11   
12     RED_0     17.499283     78.384088                 1.24   
13     RED_0     17.498648     78.388830                 1.74   
14     RED_0     17.498382     78.390789                 1.95   
15     RED_0     17.498273     78.391222                 2.00   
16     RED_0     17.498217     78.391399                 2.02   
17     RED_0     17.498146     78.391573                 2.04   
18     RED_0     17.497992     78.391890                 2.08   
19     RED_0     17.496999     78.393354                 2.27   
20     RED_0     17.496774     78.393790                 2.32   
21     RED_0     17.496619     78.394226                 2.37   
22     RED_0     17.495795     78.397290                 2.71   
23     RED_0     17.495201     78.398614                 2.87   
24     RED_0     17.494614     78.399866                 3.01   
25     RED_0     17.494044     78.401117                 3.16   
26     RED_0     17.493491     78.402364                 3.31   
27     RED_0     17.492689     78.404088                 3.51   
28     RED_0     17.492137     78.405220                 3.64   
29     RED_0     17.491611     78.406367                 3.78   
..       ...           ...           ...                  ...   
570    RED_1     17.491611     78.406367                24.23   
571    RED_1     17.492137     78.405220                24.37   
572    RED_1     17.492689     78.404088                24.50   
573    RED_1     17.493491     78.402364                24.70   
574    RED_1     17.494044     78.401117                24.85   
575    RED_1     17.494614     78.399866                25.00   
576    RED_1     17.495201     78.398614                25.15   
577    RED_1     17.495795     78.397290                25.31   
578    RED_1     17.496619     78.394226                25.65   
579    RED_1     17.496774     78.393790                25.70   
580    RED_1     17.496999     78.393354                25.75   
581    RED_1     17.497992     78.391890                25.94   
582    RED_1     17.498146     78.391573                25.98   
583    RED_1     17.498217     78.391399                26.00   
584    RED_1     17.498273     78.391222                26.02   
585    RED_1     17.498382     78.390789                26.07   
586    RED_1     17.498648     78.388830                26.28   
587    RED_1     17.499283     78.384088                26.79   
588    RED_1     17.499434     78.382950                26.91   
589    RED_1     17.499448     78.382787                26.93   
590    RED_1     17.499426     78.382398                26.97   
591    RED_1     17.499344     78.381910                27.02   
592    RED_1     17.498883     78.380592                27.17   
593    RED_1     17.497711     78.378221                27.45   
594    RED_1     17.497241     78.377090                27.58   
595    RED_1     17.496896     78.375391                27.76   
596    RED_1     17.496714     78.374809                27.82   
597    RED_1     17.496591     78.374322                27.87   
598    RED_1     17.496535     78.373836                27.92   
599    RED_1     17.496540     78.37302

## now do for BLUE line

In [8]:
route_id = 'BLU'
shapefile = 'blue.geojson'

In [9]:
shapeArray = geoJson2shape(route_id, shapefile)
dfBlu = pd.DataFrame(shapeArray)
dfBlu

Loaded blue.geojson


shape_id  shape_pt_lat  shape_pt_lon  shape_dist_traveled  \
0      BLU_0     17.390803     78.558827                 0.00   
1      BLU_0     17.392061     78.558910                 0.14   
2      BLU_0     17.393445     78.559004                 0.29   
3      BLU_0     17.394843     78.559131                 0.45   
4      BLU_0     17.395287     78.559175                 0.50   
5      BLU_0     17.395715     78.559261                 0.55   
6      BLU_0     17.395977     78.559300                 0.58   
7      BLU_0     17.396300     78.559408                 0.62   
8      BLU_0     17.396886     78.559597                 0.68   
9      BLU_0     17.398069     78.559972                 0.82   
10     BLU_0     17.398622     78.560088                 0.88   
11     BLU_0     17.398869     78.560118                 0.91   
12     BLU_0     17.399415     78.560175                 0.97   
13     BLU_0     17.400284     78.560216                 1.07   
14     BLU_0     17.400637     78.560218                 1.11   
15     BLU_0     17.401021     78.560230                 1.15   
16     BLU_0     17.401369     78.560164                 1.19   
17     BLU_0     17.401640     78.560059                 1.22   
18     BLU_0     17.401953     78.559869                 1.26   
19     BLU_0     17.402117     78.559729                 1.29   
20     BLU_0     17.402327     78.559483                 1.32   
21     BLU_0     17.402518     78.559141                 1.36   
22     BLU_0     17.402770     78.558605                 1.43   
23     BLU_0     17.402923     78.558358                 1.46   
24     BLU_0     17.403066     78.558178                 1.48   
25     BLU_0     17.403284     78.557942                 1.52   
26     BLU_0     17.405648     78.555774                 1.87   
27     BLU_0     17.408014     78.553700                 2.21   
28     BLU_0     17.408420     78.553343                 2.27   
29     BLU_0     17.408602     78.553174                 2.30   
..       ...           ...           ...                  ...   
424    BLU_1     17.408602     78.553174                14.47   
425    BLU_1     17.408420     78.553343                14.50   
426    BLU_1     17.408014     78.553700                14.56   
427    BLU_1     17.405648     78.555774                14.90   
428    BLU_1     17.403284     78.557942                15.25   
429    BLU_1     17.403066     78.558178                15.28   
430    BLU_1     17.402923     78.558358                15.30   
431    BLU_1     17.402770     78.558605                15.33   
432    BLU_1     17.402518     78.559141                15.39   
433    BLU_1     17.402327     78.559483                15.43   
434    BLU_1     17.402117     78.559729                15.47   
435    BLU_1     17.401953     78.559869                15.49   
436    BLU_1     17.401640     78.560059                15.53   
437    BLU_1     17.401369     78.560164                15.56   
438    BLU_1     17.401021     78.560230                15.60   
439    BLU_1     17.400637     78.560218                15.64   
440    BLU_1     17.400284     78.560216                15.68   
441    BLU_1     17.399415     78.560175                15.78   
442    BLU_1     17.398869     78.560118                15.84   
443    BLU_1     17.398622     78.560088                15.87   
444    BLU_1     17.398069     78.559972                15.93   
445    BLU_1     17.396886     78.559597                16.07   
446    BLU_1     17.396300     78.559408                16.14   
447    BLU_1     17.395977     78.559300                16.18   
448    BLU_1     17.395715     78.559261                16.21   
449    BLU_1     17.395287     78.559175                16.26   
450    BLU_1     17.394843     78.559131                16.31   
451    BLU_1     17.393445     78.559004                16.47   
452    BLU_1     17.392061     78.558910                16.62   
453    BLU_1     17.390803     78.55882

## now concat the two df's and write out to shape.txt (csv format)

In [10]:
df = pd.concat([dfRed, dfBlu],ignore_index=True)

In [12]:
df.to_csv(outputFolder + 'shapes.txt', index=False)